# 

# module

In [80]:
def get_dendrogram_segments(icoord, dcoord):
    """Linkage Matrixから描画用セグメントを生成。簡易実装。"""
  
    segments = []
    for icoords, dcoords in zip(icoord, dcoord):
        x1, x2, x3, x4 = icoords
        y1, y2, y3, y4 = dcoords
        segments.append([(x1, y1), (x2, y2)])
        segments.append([(x2, y2), (x3, y3)])
        segments.append([(x4, y4), (x3, y3)])
    return segments

In [81]:
import plotly.graph_objects as go
import plotly.graph_objects as go
HIGHLIGHT_COLORS = {
    'default': 'skyblue',
    'dr_selection': 'orange',
    'heatmap_click': 'red',
}
def plot_dendrogram_plotly(segments, 
                           colors=None, 
                           scores=None, 
                           is_selecteds=None,
                           is_heatmap_clicked=None,
                           **kwargs):
    """Plotlyを使用したデンドログラムの描画（segmentsは線分タプルのリスト）"""

    # kwargsに含まれる情報が有効かチェック
    additional_data = []
    
    # kwargs内のリストも展開して保存
    for key, value_list in kwargs.items():
        
        # ✅ 有効なリストは3倍に展開してadditional_dataに追加
    
        additional_data.append((key, value_list))
        print(f"length of expanded {key}: {len(value_list)}")
    
  
    fig = go.Figure()
    for i, seg in enumerate(segments):
        index = i // 3  # 3つのセグメントごとに1つのクラスタに対応
       
        x_coords = [seg[0][0], seg[1][0]]
        y_coords = [seg[0][1], seg[1][1]]
        # 色設定の優先順位: heatmapクリック > DR選択 > デフォルト
        opacity = 1.0
        
        # heatmapクリックが最優先
        if is_heatmap_clicked is not None and is_heatmap_clicked[index]:
            color = HIGHLIGHT_COLORS['heatmap_click']
        elif is_selecteds is not None and is_selecteds[index]:
            color = HIGHLIGHT_COLORS['dr_selection']
        else:
            color = HIGHLIGHT_COLORS['default']

        hover_lines = []
        for key, value_list in additional_data:
            value = value_list[index] if index < len(value_list) else "N/A"
            if isinstance(value, float):
                hover_lines.append(f"{key}: {value:.4f}")
            else:
                hover_lines.append(f"{key}: {value}")
        
        full_hover_text = '<br>'.join(hover_lines)
        
        fig.add_trace(go.Scatter(
            x=x_coords,
            y=y_coords,
            mode='lines',
            line=dict(color=color, width=1),
            showlegend=False,
            hoverinfo='text' if (is_selecteds is None or is_selecteds[index]) else 'skip',
            text=[full_hover_text] * len(x_coords),
            opacity=opacity
        ))

    return fig

In [ ]:
def _get_leaves(condensed_tree):
    cluster_tree = condensed_tree[condensed_tree['child_size'] > 1]
    print(len(cluster_tree))
    if cluster_tree.shape[0] == 0:
        # Return the only cluster, the root
        return [condensed_tree['parent'].min()]

    root = cluster_tree['parent'].min()
    return _recurse_leaf_dfs(cluster_tree, root)
  
def _recurse_leaf_dfs(cluster_tree, current_node):
  children = cluster_tree[cluster_tree['parent'] == current_node]['child']
  if len(children) == 0:
      return [current_node,]
  else:
      return sum([_recurse_leaf_dfs(cluster_tree, child) for child in children], [])
  
def get_leaves(cluster_tree):
    """
    cluster_tree: (u, v, lambda_val, child_size, parent)
    """
    root = cluster_tree[:, 2].max()
    print(f"root: {root}")
    return recurse_leaf_dfs(cluster_tree, root)
    

def recurse_leaf_dfs(cluster_tree, current_node):
    # print(f"Visiting Node: {current_node}")
    child1 = cluster_tree[cluster_tree[:,2] == current_node][:,0]
    child2 = cluster_tree[cluster_tree[:,2] == current_node][:,1]
    # print(f"Children of Node {current_node}: Child1 {child1}, Child2 {child2}")

    if len(child1) == 0 and len(child2) == 0:
        
        return [current_node,]
    else:
        return sum([recurse_leaf_dfs(cluster_tree, child) for child in np.concatenate((child1, child2))], [])


def get_linkage_matrix_from_hdbscan(condensed_tree):
    """
    (child1, child2, parent, lambda_val, count)
    """
    print("Generating linkage matrix from HDBSCAN condensed tree...")
    linkage_matrix = []
    raw_tree = condensed_tree._raw_tree
    condensed_tree = condensed_tree.to_pandas()
    cluster_tree = condensed_tree[condensed_tree['child_size'] > 1]
    sorted_condensed_tree = cluster_tree.sort_values(by=['lambda_val','parent'], ascending=True)
    print(f"len of sorted condensed tree: {len(sorted_condensed_tree)}")

    for i in range(0, len(sorted_condensed_tree), 2):
    
        # 偶数行（i）と次の奇数行（i+1）をペアとして取得
        if i + 1 < len(sorted_condensed_tree):
            
            row_a = sorted_condensed_tree.iloc[i]
            row_b = sorted_condensed_tree.iloc[i+1]
            
            # **前提チェック**: lambda_valが同じであることを確認
            if row_a['lambda_val'] != row_b['lambda_val']:
                # lambda_valが異なる場合は、次の処理に進む（結合の前提が崩れる）
                raise ValueError(f"Lambda value mismatch at rows {i} and {i+1}: {row_a['lambda_val']} vs {row_b['lambda_val']}")
                
            # Parent IDが同じであることを確認 (同じ結合の結果である可能性が高い)
            if row_a['parent'] != row_b['parent']:
                # Parent IDが異なる場合は、このペアは単一の結合ではない可能性が高い
                raise ValueError(f"Parent ID mismatch at rows {i} and {i+1}: {row_a['parent']} vs {row_b['parent']}")
            
            child_a = row_a['child']
            child_b = row_b['child']
            lam = row_a['lambda_val']
            
            # count (サイズ) は、結合された2つの子ノードのサイズ合計を使うのが論理的だが、
            # HDBSCANは親ノードのサイズをリストで持っているため、ここではそのサイズを使用
            # より正確には、このParent IDを持つ全子ノードのサイズの合計を使うべきだが、
            # 2行の child_size の合計で暫定的に対応
            # total_size = row_a['child_size'] + row_b['child_size']


            total_size = raw_tree[raw_tree['child'] == row_a['parent']]['child_size']
            if len(total_size) == 0:
                total_size = row_a['child_size'] + row_b['child_size']
            else:
                total_size = total_size[0]
            # print(total_size)
            parent_id = row_a['parent']

            linkage_matrix.append([
                int(child_a), 
                int(child_b), 
                int(parent_id),
                lam, 
                total_size,
        ])   
    print(f"len of linkage matrix: {len(linkage_matrix)}")


    # 葉ノードに0-N-1のIDを振る
    node_id_map = {}
    current_id = 0
    leaves = _get_leaves(raw_tree)
    print(f"Number of leaves: {len(leaves)}")

    for leaf in leaves:
        node_id_map[int(leaf)] = current_id
        current_id += 1

    print(f"Leaf ID Map Size: {len(node_id_map)}")
    print(f"current id: {current_id}")

    # 結合ノードにIDを振る(linkage matrixのparent)
    for row in linkage_matrix.__reversed__():
        parent_id = row[2]
        if parent_id not in node_id_map:
            node_id_map[parent_id] = current_id
            current_id += 1

        else:
            print(f"Duplicate Parent ID found: {parent_id}")
            raise ValueError(f"Node ID {parent_id} already assigned!")
    print(f"Total Node ID Map Size: {len(node_id_map)}")
    print(f"current_id: {current_id}")

    # linkage matrixを書き換え
    max_lambda = max(row[3] for row in linkage_matrix)
    print(f"Max Lambda: {max_lambda}")
    linkage_matrix_mapped = [ 
        [node_id_map[row[0]], node_id_map[row[1]], node_id_map[row[2]], max_lambda - row[3], row[4]] 
        for row in linkage_matrix.__reversed__()
    ]

    return np.array(linkage_matrix_mapped), node_id_map # linkage matrix, parentid -> newid



# data

In [5]:
from sklearn.datasets import make_blobs
from sklearn.metrics import pairwise_distances
import hdbscan
import numpy as np

N_LARGE = 1000

# 1. データの生成
# 4つのクラスタを持つ100点のデータ
X_large, y_large = make_blobs(n_samples=N_LARGE, centers=4, cluster_std=1.0, random_state=42)

# 2. HDBSCANの適用とLinkage Matrixの取得
# min_cluster_sizeを小さく設定し、すべてのデータ点が階層構造に含まれるようにする
clusterer_large = hdbscan.HDBSCAN(min_cluster_size=2, prediction_data=True).fit(X_large)

# hdbscanのCondensed TreeからScipy形式のLinkage Matrix (Z) に変換
# Z_large は (N-1) x 4 の行列になります
Z_large = get_linkage_matrix_from_hdbscan(clusterer_large.condensed_tree_)[0]


# 3. 類似度（距離）行列の計算
# 全てのデータ点間のユークリッド距離を計算
leaf_distances_large = pairwise_distances(X_large, metric='euclidean')

n_clusters = Z_large.shape[0] + 1


print(f"\n--- N={N_LARGE} データセット ---")
print(f"Z_large shape: {Z_large.shape}")
print(f"leaf_distances_large shape: {leaf_distances_large.shape}")
print(f"n_clusters: {n_clusters}")


Generating linkage matrix from HDBSCAN condensed tree...
len of sorted condensed tree: 320
len of linkage matrix: 160
320
Number of leaves: 161
Leaf ID Map Size: 161
current id: 161
Total Node ID Map Size: 321
current_id: 321
Max Lambda: 11.872544219858835

--- N=1000 データセット ---
Z_large shape: (160, 5)
leaf_distances_large shape: (1000, 1000)
n_clusters: 161


/Library/Frameworks/Python.framework/Versions/3.12/lib/python3.12/site-packages/sklearn/utils/deprecation.py:132: FutureWarning: 'force_all_finite' was renamed to 'ensure_all_finite' in 1.6 and will be removed in 1.8.
  warnings.warn(
/Library/Frameworks/Python.framework/Versions/3.12/lib/python3.12/site-packages/sklearn/utils/deprecation.py:132: FutureWarning: 'force_all_finite' was renamed to 'ensure_all_finite' in 1.6 and will be removed in 1.8.
  warnings.warn(


In [9]:
import numpy as np

def compute_dendrogram_coords(Z, n_points, leaf_distances=None, sort_by='size'):
    """
    Linkage Matrixからデンドログラム描画用の座標を計算
    Z: (n_merges x 4) array like [c1, c2, dist, count]
    n_points: 葉の数
    leaf_distances: (n_points x n_points) array. 葉のインデックス間の距離行列。
                    sort_by='optimal'の場合に必要。
    sort_by: 'size' (クラスタサイズでソート) または 'optimal' (類似度でソート)

    Returns: icoord, dcoord, leaf_order
    """
    # --- 1. ノード情報の準備 (省略) ---
    n_nodes = 2 * n_points - 1
   
    nodes = [{'x': None, 'y': 0.0, 'size': 1, 'left': None, 'right': None} for _ in range(n_points)]

    for i in range(n_points - 1):
        c1, c2, dist, count = Z[i]
        nodes.append({
            'x': None,
            'y': float(dist),
            'size': int(count),
            'left': int(c1),
            'right': int(c2)
        })

    # --- 2. ソートロジックの定義 ---
    
    def get_leaf_order_sorted(node_idx):
        node = nodes[node_idx]
        if node_idx < n_points:
            # リーフノードの場合
            return [node_idx]
        
        
        
        C1_idx, C2_idx = node['left'], node['right']

        if C1_idx == node_idx or C2_idx == node_idx:
             print(f"Self-reference detected at node {node_idx}")
             print(f"right: {C2_idx}, left: {C1_idx}")
             raise ValueError(f"Self-reference detected at node {node_idx}")

        # 左右の枝に含まれるリーフノードの順序を再帰的に取得
        order_C1 = get_leaf_order_sorted(C1_idx)
        order_C2 = get_leaf_order_sorted(C2_idx)
        
        # --- ソート（枝の回転）の決定 ---
        should_swap = False
        
        if sort_by == 'size':
            # 既存のロジック: サイズの大きい方を左に (size_C1 < size_C2 なら交換)
            size_C1, size_C2 = nodes[C1_idx]['size'], nodes[C2_idx]['size']
            if size_C1 < size_C2:
                should_swap = True

        elif sort_by == 'optimal' and leaf_distances is not None:
            # 類似度に基づくソート (Optimal Leaf Orderingのシミュレーション)
            # 左右の枝の内側のリーフ間の距離を比較する (回転前 vs 回転後)
            
            # 回転前: C1の右端のリーフと C2の左端のリーフ の距離
            dist_normal = leaf_distances[order_C1[-1], order_C2[0]]
            
            # 回転後: C2の右端のリーフと C1の左端のリーフ の距離
            dist_swapped = leaf_distances[order_C2[-1], order_C1[0]]
            
            # 回転後の方が近ければ交換
            if dist_swapped < dist_normal:
                should_swap = True
                
        # 枝の交換を実行
        if should_swap:
            return order_C2 + order_C1
        else:
            return order_C1 + order_C2
        
    def calculate_x_coord(node_idx, leaf_to_x):
        node = nodes[node_idx]
        if node_idx < n_points:
            x_coord = leaf_to_x[node_idx]
            node['x'] = x_coord
            return x_coord
        x_left = calculate_x_coord(node['left'], leaf_to_x)
        x_right = calculate_x_coord(node['right'], leaf_to_x)
        x_coord = (x_left + x_right) / 2.0
        node['x'] = x_coord
        return x_coord

    # --- 3. デンドログラム座標の計算 (省略) ---
    root_node_idx = n_points - 1 + (n_points - 1)
    leaf_order = get_leaf_order_sorted(root_node_idx)
    
    # ... (X座標の計算とicoord, dcoordの構築は既存ロジックをそのまま使用) ...
    # 省略部分は変更なし
    leaf_to_x = {leaf_idx: 2 * i + 1 for i, leaf_idx in enumerate(leaf_order)}
    calculate_x_coord(root_node_idx, leaf_to_x)

    icoord = []
    dcoord = []
    for i in range(n_points - 1):
        P = n_points + i
        C1 = nodes[P]['left']
        C2 = nodes[P]['right']
        y_P = nodes[P]['y']
        y_C1 = nodes[C1]['y']
        y_C2 = nodes[C2]['y']
        x_P = nodes[P]['x']
        x_C1 = nodes[C1]['x']
        x_C2 = nodes[C2]['x']
        icoord.append([x_C1, x_C1, x_C2, x_C2])
        dcoord.append([y_C1, y_P, y_P, y_C2])

    return icoord, dcoord, leaf_order

In [36]:
import sys

# recursion limitを増やす
sys.setrecursionlimit(2000)

In [ ]:

icoord, dcoord, leaf_order = compute_dendrogram_coords(Z_large[:, [0,1,3,4]], n_clusters , leaf_distances=leaf_distances_large, sort_by='size')
segments = get_dendrogram_segments(icoord, dcoord)
plot_dendrogram_plotly(segments).show()

icoord, dcoord, leaf_order = compute_dendrogram_coords(Z_large[:, [0,1,3,4]], n_clusters , leaf_distances=leaf_distances_large, sort_by='optimal')
segments = get_dendrogram_segments(icoord, dcoord)
plot_dendrogram_plotly(segments).show()

In [6]:
def compute_dendrogram_coords_2(Z, n_points, leaf_distances=None, sort_by='size'):
    """
    Linkage Matrixからデンドログラム描画用の座標を計算
    ... (ドキュメンテーションは省略) ...
    """
    # --- 1. ノード情報の準備 (変更なし) ---
    n_nodes = 2 * n_points - 1
    nodes = [{'x': None, 'y': 0.0, 'size': 1, 'left': None, 'right': None} for _ in range(n_points)]

    for i in range(n_points - 1):
        c1, c2, dist, count = Z[i]
        nodes.append({
            'x': None,
            'y': float(dist),
            'size': int(count),
            'left': int(c1),
            'right': int(c2)
        })

    # --- 2. ソートロジックの定義 (変更部分) ---
    
    def get_leaf_order_sorted(node_idx):
        node = nodes[node_idx]
        if node_idx < n_points:
            return [node_idx]
        
        C1_idx, C2_idx = node['left'], node['right']

        # 左右の枝に含まれるリーフノードの順序を再帰的に取得
        order_C1 = get_leaf_order_sorted(C1_idx)
        order_C2 = get_leaf_order_sorted(C2_idx)
        
        # --- 枝の交換決定ロジック ---
        
        # 初期状態: C1が左、C2が右
        current_C1, current_C2 = order_C1, order_C2

        # 1. 第一段階: サイズソート (size) を適用
        # サイズが大きい方を左に配置する
        if nodes[C1_idx]['size'] < nodes[C2_idx]['size']:
            # サイズソート基準で交換が必要
            current_C1, current_C2 = order_C2, order_C1 # 交換を実行 (サイズソートの結果を保持)
        # else: サイズが大きい方を左にするため交換なし
        
        final_order = current_C1 + current_C2 # サイズソート後の暫定順序

        # 2. 第二段階: 類似度ソート (optimal) を適用（sort_by='optimal'が指定された場合）
        if sort_by == 'optimal' and leaf_distances is not None:
            
            # --- ここで、類似度ソートのロジックを適用し、結果を上書き ---
            
            # 枝のサイズを無視し、類似度のみに基づいて交換が必要か判定する
            
            # 回転前: C1の右端と C2の左端 の距離
            dist_normal = leaf_distances[order_C1[-1], order_C2[0]]
            
            # 回転後: C2の右端と C1の左端 の距離
            dist_swapped = leaf_distances[order_C2[-1], order_C1[0]]
            
            # 類似度ソート基準で交換後の方が近ければ、サイズソートの結果を無視して交換
            if dist_swapped < dist_normal:
                final_order = order_C2 + order_C1 # 類似度基準で交換された順序
            else:
                final_order = order_C1 + order_C2 # 類似度基準で交換されない順序

        # サイズソート単独、または類似度ソート単独（指定された場合）の結果を返す
        # 上記のロジックは、sizeソートの結果を類似度ソートが上書きする形になります。
        return final_order
    
    def calculate_x_coord(node_idx, leaf_to_x):
        node = nodes[node_idx]
        if node_idx < n_points:
            x_coord = leaf_to_x[node_idx]
            node['x'] = x_coord
            return x_coord
        x_left = calculate_x_coord(node['left'], leaf_to_x)
        x_right = calculate_x_coord(node['right'], leaf_to_x)
        x_coord = (x_left + x_right) / 2.0
        node['x'] = x_coord
        return x_coord

    # --- 3. デンドログラム座標の計算 (変更なし) ---
    root_node_idx = n_points - 1 + (n_points - 1)
    leaf_order = get_leaf_order_sorted(root_node_idx)
    
    # ... (X座標の計算とicoord, dcoordの構築は既存ロジックをそのまま使用) ...
    # 省略部分は変更なし
    leaf_to_x = {leaf_idx: 2 * i + 1 for i, leaf_idx in enumerate(leaf_order)}
    calculate_x_coord(root_node_idx, leaf_to_x)

    icoord = []
    dcoord = []
    for i in range(n_points - 1):
        P = n_points + i
        C1 = nodes[P]['left']
        C2 = nodes[P]['right']
        y_P = nodes[P]['y']
        y_C1 = nodes[C1]['y']
        y_C2 = nodes[C2]['y']
        x_P = nodes[P]['x']
        x_C1 = nodes[C1]['x']
        x_C2 = nodes[C2]['x']
        icoord.append([x_C1, x_C1, x_C2, x_C2])
        dcoord.append([y_C1, y_P, y_P, y_C2])

    return icoord, dcoord, leaf_order


In [30]:
icoord, dcoord, leaf_order = compute_dendrogram_coords_2(Z_large[:, [0,1,3,4]], n_clusters, leaf_distances=leaf_distances_large, sort_by='optimal')
segments = get_dendrogram_segments(icoord, dcoord)
plot_dendrogram_plotly(segments).show()

icoord, dcoord, leaf_order = compute_dendrogram_coords(Z_large[:, [0,1,3,4]], n_clusters, leaf_distances=leaf_distances_large, sort_by='optimal')
segments = get_dendrogram_segments(icoord, dcoord)
plot_dendrogram_plotly(segments).show()

# a

In [167]:
import pickle
with open('../18_rapids/result/20251203_053328/condensed_tree_object.pkl', 'rb') as f:
    condensed_tree = pickle.load(f)

with open('../19_tree/processed_data/cluster_similarities.pkl', 'rb') as f:
    cluster_similarities = pickle.load(f)

print(cluster_similarities.keys())
linkage_matrix, cluster_to_id_map = get_linkage_matrix_from_hdbscan(condensed_tree)
n_clusters = linkage_matrix.shape[0] + 1
print(f"cluster n : {n_clusters}")
cluster_similarity_dict = cluster_similarities["mahalanobis_distance"]


# reverse
id_to_cluster_map = {k: v for v, k in cluster_to_id_map.items()}
print(f"head map:{list(id_to_cluster_map.items())[:5]}")

# make cluster similarity matrix
# cluster id, cluster id -> linkage matrix id

cluster_similarity = np.zeros((n_clusters, n_clusters))

import numpy as np

# --- 前提 ---
# n_clusters: リーフノードの総数 N
# cluster_similarity: N x N の numpy.zeros 行列
# cluster_similarity_dict: {(l1, l2): distance} 形式の辞書
# id_to_cluster_map: {cluster_index (0~N-1): cluster_id (l1, l2で使用)} 形式の辞書
# ------------------

# 対角成分の処理を含めるため、ループ後に np.fill_diagonal を実行する方が簡潔です。
# ただし、ここではご要望通り、ループ内で値を設定します。
for cluster1 in range(n_clusters):
    for cluster2 in range(n_clusters):
        
        # 自身との距離（対角成分）は必ず0に設定
        if cluster1 == cluster2:
            cluster_similarity[cluster1, cluster2] = 0.0
            continue # 次のループへ

        l1 = id_to_cluster_map.get(cluster1)
        l2 = id_to_cluster_map.get(cluster2)
        
        # 1. 最初に (l1, l2) の順で値を取得を試みる
        similarity = cluster_similarity_dict.get((l1, l2))
        
        # 2. 値が None（キーが存在しない）の場合、キーを反転して (l2, l1) の順で検索
        if similarity is None:
             # 反転キー (l2, l1) で検索。それでも見つからなければ 0.0 とする。
             similarity = cluster_similarity_dict.get((l2, l1), 0.0)

        # 3. 行列への代入と対称性の確保
        
        # 行列の (cluster1, cluster2) に値を代入
        cluster_similarity[cluster1, cluster2] = similarity
        
        # 対称性の確保: (cluster2, cluster1) にも同じ値を代入
        # これにより、行列全体が対称になります。
        cluster_similarity[cluster2, cluster1] = similarity


print(f"head similarity: {cluster_similarity[:5, :5]}")


dict_keys(['kl_divergence', 'bhattacharyya_coefficient', 'mahalanobis_distance'])
Generating linkage matrix from HDBSCAN condensed tree...
len of sorted condensed tree: 884
len of linkage matrix: 442
884
Number of leaves: 443
Leaf ID Map Size: 443
current id: 443
Total Node ID Map Size: 885
current_id: 885
Max Lambda: 2.4746105670928955
cluster n : 443
head map:[(0, 115760), (1, 115763), (2, 115769), (3, 115771), (4, 115774)]
head similarity: [[  0.          56.91189655  58.49257851 135.87115276  30.79106656]
 [ 56.91189655   0.          11.79247147  10.00750598   7.55256419]
 [ 58.49257851  11.79247147   0.          16.13170821   4.30812969]
 [135.87115276  10.00750598  16.13170821   0.           7.3173488 ]
 [ 30.79106656   7.55256419   4.30812969   7.3173488    0.        ]]


In [57]:
def compute_dendrogram_coords_no_sort(Z, n_points):
    """
    Linkage Matrixからデンドログラム描画用の座標を計算します。
    枝の回転（ソート）は一切行いません。Z行列の結合順序通りに配置します。

    Z: (n_merges x 4) array like [c1, c2, dist, count]
    n_points: 葉の数

    Returns: icoord, dcoord, leaf_order
    """
    # --- 1. ノード情報の準備 ---
    n_nodes = 2 * n_points - 1
    nodes = [{'x': None, 'y': 0.0, 'size': 1, 'left': None, 'right': None} for _ in range(n_points)]

    # Z の各行は c1, c2, dist, count
    for i in range(n_points - 1):
        c1, c2, dist, count = Z[i]
        nodes.append({
            'x': None,
            'y': float(dist),
            'size': int(count),
            'left': int(c1),
            'right': int(c2)
        })

    # --- 2. ソートロジックなしの順序取得 ---
    
    def get_leaf_order_no_sort(node_idx):
        node = nodes[node_idx]
        if node_idx < n_points:
            # リーフノードの場合、自身のIDを返す（再帰の終了条件）
            return [node_idx]
        
        C1_idx, C2_idx = node['left'], node['right']
        
        # Z 行列に記録された C1, C2 の順序をそのまま保持し、回転しない
        order_left = get_leaf_order_no_sort(C1_idx)
        order_right = get_leaf_order_no_sort(C2_idx)
        
        return order_left + order_right

    # --- 3. 座標の計算 ---
    
    def calculate_x_coord(node_idx, leaf_to_x):
        node = nodes[node_idx]
        if node_idx < n_points:
            x_coord = leaf_to_x[node_idx]
            node['x'] = x_coord
            return x_coord
        x_left = calculate_x_coord(node['left'], leaf_to_x)
        x_right = calculate_x_coord(node['right'], leaf_to_x)
        x_coord = (x_left + x_right) / 2.0
        node['x'] = x_coord
        return x_coord
    
    root_node_idx = n_points - 1 + (n_points - 1)
    
    # ソートなしでリーフの順序を取得
    leaf_order = get_leaf_order_no_sort(root_node_idx)
    
    # リーフの順序に基づいてX座標を割り当て
    leaf_to_x = {leaf_idx: 2 * i + 1 for i, leaf_idx in enumerate(leaf_order)}
    calculate_x_coord(root_node_idx, leaf_to_x)

    # --- 4. 座標情報の抽出 ---
    icoord = []
    dcoord = []
    for i in range(n_points - 1):
        P = n_points + i
        C1 = nodes[P]['left']
        C2 = nodes[P]['right']
        y_P = nodes[P]['y']
        y_C1 = nodes[C1]['y']
        y_C2 = nodes[C2]['y']
        x_P = nodes[P]['x']
        x_C1 = nodes[C1]['x']
        x_C2 = nodes[C2]['x']
        
        # デンドログラムの垂直線と水平線を定義
        icoord.append([x_C1, x_C1, x_C2, x_C2])
        dcoord.append([y_C1, y_P, y_P, y_C2])

    return icoord, dcoord, leaf_order

In [59]:
icoord, dcoord, leaf_order = compute_dendrogram_coords(linkage_matrix[:, [0,1,3,4]], n_clusters, leaf_distances=cluster_similarity, sort_by='optimal')
segments = get_dendrogram_segments(icoord, dcoord)
plot_dendrogram_plotly(segments).show()



icoord, dcoord, leaf_order = compute_dendrogram_coords_no_sort(linkage_matrix[:, [0,1,3,4]], n_clusters)
segments = get_dendrogram_segments(icoord, dcoord)
plot_dendrogram_plotly(segments).show()

In [ ]:

def compute_dendrogram_coords_2(Z, n_points, leaf_distances=None, sort_by='size'):
    """
    Linkage Matrixからデンドログラム描画用の座標を計算
    ... (ドキュメンテーションは省略) ...
    """
    # --- 1. ノード情報の準備 (変更なし) ---
    n_nodes = 2 * n_points - 1
    nodes = [{'x': None, 'y': 0.0, 'size': 1, 'left': None, 'right': None} for _ in range(n_points)]

    for i in range(n_points - 1):
        c1, c2, dist, count = Z[i]
        nodes.append({
            'x': None,
            'y': float(dist),
            'size': int(count),
            'left': int(c1),
            'right': int(c2)
        })

    # --- 2. ソートロジックの定義 (変更部分) ---
    
    def get_leaf_order_sorted(node_idx):
        node = nodes[node_idx]
        if node_idx < n_points:
            return [node_idx]
        
        C1_idx, C2_idx = node['left'], node['right']

        # 左右の枝に含まれるリーフノードの順序を再帰的に取得
        order_C1 = get_leaf_order_sorted(C1_idx)
        order_C2 = get_leaf_order_sorted(C2_idx)
        
        # --- 枝の交換決定ロジック ---
        
        # 初期状態: C1が左、C2が右
        current_C1, current_C2 = order_C1, order_C2

        # 1. 第一段階: サイズソート (size) を適用
        # サイズが大きい方を左に配置する
        if nodes[C1_idx]['size'] < nodes[C2_idx]['size']:
            # サイズソート基準で交換が必要
            current_C1, current_C2 = order_C2, order_C1 # 交換を実行 (サイズソートの結果を保持)
        # else: サイズが大きい方を左にするため交換なし
        
        final_order = current_C1 + current_C2 # サイズソート後の暫定順序

        # 2. 第二段階: 類似度ソート (optimal) を適用（sort_by='optimal'が指定された場合）
        if sort_by == 'optimal' and leaf_distances is not None:
            
            # --- ここで、類似度ソートのロジックを適用し、結果を上書き ---
            
            # 枝のサイズを無視し、類似度のみに基づいて交換が必要か判定する
            
            # 回転前: C1の右端と C2の左端 の距離
            dist_normal = leaf_distances[order_C1[-1], order_C2[0]]
            
            # 回転後: C2の右端と C1の左端 の距離
            dist_swapped = leaf_distances[order_C2[-1], order_C1[0]]
            
            # 類似度ソート基準で交換後の方が近ければ、サイズソートの結果を無視して交換
            if dist_swapped < dist_normal:
                final_order = order_C2 + order_C1 # 類似度基準で交換された順序
            else:
                final_order = order_C1 + order_C2 # 類似度基準で交換されない順序

        # サイズソート単独、または類似度ソート単独（指定された場合）の結果を返す
        # 上記のロジックは、sizeソートの結果を類似度ソートが上書きする形になります。
        return final_order
    
    def calculate_x_coord(node_idx, leaf_to_x):
        node = nodes[node_idx]
        if node_idx < n_points:
            x_coord = leaf_to_x[node_idx]
            node['x'] = x_coord
            return x_coord
        x_left = calculate_x_coord(node['left'], leaf_to_x)
        x_right = calculate_x_coord(node['right'], leaf_to_x)
        x_coord = (x_left + x_right) / 2.0
        node['x'] = x_coord
        return x_coord

    # --- 3. デンドログラム座標の計算 (変更なし) ---
    root_node_idx = n_points - 1 + (n_points - 1)
    leaf_order = get_leaf_order_sorted(root_node_idx)
    
    # ... (X座標の計算とicoord, dcoordの構築は既存ロジックをそのまま使用) ...
    # 省略部分は変更なし
    leaf_to_x = {leaf_idx: 2 * i + 1 for i, leaf_idx in enumerate(leaf_order)}
    calculate_x_coord(root_node_idx, leaf_to_x)

    icoord = []
    dcoord = []
    for i in range(n_points - 1):
        P = n_points + i
        C1 = nodes[P]['left']
        C2 = nodes[P]['right']
        y_P = nodes[P]['y']
        y_C1 = nodes[C1]['y']
        y_C2 = nodes[C2]['y']
        x_P = nodes[P]['x']
        x_C1 = nodes[C1]['x']
        x_C2 = nodes[C2]['x']
        icoord.append([x_C1, x_C1, x_C2, x_C2])
        dcoord.append([y_C1, y_P, y_P, y_C2])

    return icoord, dcoord, leaf_order

In [56]:
icoord, dcoord, leaf_order = compute_dendrogram_coords(linkage_matrix[:, [0,1,3,4]], n_clusters, leaf_distances=cluster_similarity, sort_by='optimal')
segments = get_dendrogram_segments(icoord, dcoord)
plot_dendrogram_plotly(segments).show()

icoord, dcoord, leaf_order = compute_dendrogram_coords(linkage_matrix[:, [0,1,3,4]], n_clusters, leaf_distances=cluster_similarity, sort_by='size')
segments = get_dendrogram_segments(icoord, dcoord)
plot_dendrogram_plotly(segments).show()

icoord, dcoord, leaf_order = compute_dendrogram_coords_2(linkage_matrix[:, [0,1,3,4]], n_clusters, leaf_distances=cluster_similarity, sort_by='optimal')
segments = get_dendrogram_segments(icoord, dcoord)
plot_dendrogram_plotly(segments).show()

In [88]:
def compute_dendrogram_coords_2(
        Z,
        n_points,
        leaf_distances=None,
        sort_by='size',
        bottom_up=False,
        allow_cross=True
    ):
    """
    Linkage Matrixからデンドログラム描画用の座標を計算
    bottom_up=True  → ボトムアップ並べ替え
    allow_cross=True → トップダウン時に交差を許す
    """

    # --- 1. ノード構造準備 ---
    n_nodes = 2 * n_points - 1
    nodes = [{'x': None, 'y': 0.0, 'size': 1, 'left': None, 'right': None}
             for _ in range(n_points)]

    for i in range(n_points - 1):
        c1, c2, dist, count = Z[i]
        nodes.append({
            'x': None,
            'y': float(dist),
            'size': int(count),
            'left': int(c1),
            'right': int(c2)
        })


    # --- 2. 並べ替えロジック ---
    def order_bottom_up(node_idx):
        """ボトムアップの葉順序"""
        node = nodes[node_idx]
        if node_idx < n_points:
            return [node_idx]

        C1, C2 = node['left'], node['right']
        L1 = order_bottom_up(C1)
        L2 = order_bottom_up(C2)

        # 距離がない場合はサイズ優先
        if leaf_distances is None:
            if nodes[C1]['size'] < nodes[C2]['size']:
                return L2 + L1
            else:
                return L1 + L2

        # 類似度
        dist_normal = leaf_distances[L1[-1], L2[0]]
        dist_swapped = leaf_distances[L2[-1], L1[0]]

        if allow_cross:  # 交差あり → スワップを許す
            if dist_swapped < dist_normal:
                return L2 + L1
            else:
                return L1 + L2
        else:  # 交差なし
            return L1 + L2


    def order_top_down(node_idx):
        """トップダウンの葉順序（あなたの既存ロジック + 交差許可条件）"""
        node = nodes[node_idx]
        if node_idx < n_points:
            return [node_idx]

        C1_idx, C2_idx = node['left'], node['right']
        order_C1 = order_top_down(C1_idx)
        order_C2 = order_top_down(C2_idx)

        # サイズによる初期ソート
        if sort_by == 'size':
            if nodes[C1_idx]['size'] < nodes[C2_idx]['size']:
                order_C1, order_C2 = order_C2, order_C1

        # 類似度最適化
        if sort_by == 'optimal' and leaf_distances is not None:
            dist_normal = leaf_distances[order_C1[-1], order_C2[0]]
            dist_swapped = leaf_distances[order_C2[-1], order_C1[0]]

            if allow_cross:  # 交差を許すときだけ swap を採用
                if dist_swapped < dist_normal:
                    order_C1, order_C2 = order_C2, order_C1

        return order_C1 + order_C2


    # --- 3. 実際に使用する並べ替え ---
    root_node_idx = n_points - 1 + (n_points - 1)

    if bottom_up:
        print("Using bottom-up ordering...")
        leaf_order = order_bottom_up(root_node_idx)
    else:
        print("Using top-down ordering...")
        leaf_order = order_top_down(root_node_idx)


    # --- 4. X座標計算 ---
    leaf_to_x = {leaf_idx: 2 * i + 1 for i, leaf_idx in enumerate(leaf_order)}

    def calculate_x_coord(node_idx):
        node = nodes[node_idx]
        if node_idx < n_points:
            node['x'] = leaf_to_x[node_idx]
            return node['x']

        xL = calculate_x_coord(node['left'])
        xR = calculate_x_coord(node['right'])
        node['x'] = (xL + xR) / 2
        return node['x']

    calculate_x_coord(root_node_idx)

    # --- 5. icoord, dcoord を構築 ---
    icoord = []
    dcoord = []

    for i in range(n_points - 1):
        P = n_points + i
        C1 = nodes[P]['left']
        C2 = nodes[P]['right']

        x_P = nodes[P]['x']
        y_P = nodes[P]['y']
        x_C1 = nodes[C1]['x']
        x_C2 = nodes[C2]['x']
        y_C1 = nodes[C1]['y']
        y_C2 = nodes[C2]['y']

        icoord.append([x_C1, x_C1, x_C2, x_C2])
        dcoord.append([y_C1, y_P, y_P, y_C2])

    return icoord, dcoord, leaf_order


In [93]:
def compute_dendrogram_coords_bottom_up(Z, n_points, leaf_distances=None, sort_by='size'):
    """
    Linkage Matrixからデンドログラム描画用の座標を計算します。
    枝の回転（ソート）は、ボトムアップ（再帰の戻りがけ）で行われます。
    
    sort_by='optimal'を指定すると、サイズソートを無視し、類似度に基づいて回転を決定します。
    """
    # --- 1. ノード情報の準備 (変更なし) ---
    n_nodes = 2 * n_points - 1
    nodes = [{'x': None, 'y': 0.0, 'size': 1, 'left': None, 'right': None} for _ in range(n_points)]

    for i in range(n_points - 1):
        c1, c2, dist, count = Z[i]
        nodes.append({
            'x': None,
            'y': float(dist),
            'size': int(count),
            'left': int(c1),
            'right': int(c2)
        })

    # --- 2. ソートロジックの定義 (修正部分) ---
    
    def get_leaf_order_sorted(node_idx):
        node = nodes[node_idx]
        if node_idx < n_points:
            return [node_idx]
        
        C1_idx, C2_idx = node['left'], node['right']

        # 左右の枝に含まれるリーフノードの順序を再帰的に取得
        # **再帰により、まず最下層の順序が確定する (ボトムアップ処理)**
        order_C1 = get_leaf_order_sorted(C1_idx)
        order_C2 = get_leaf_order_sorted(C2_idx)
        
        # --- 枝の交換決定ロジック ---
        
        final_order = order_C1 + order_C2 # デフォルト順序（交換なし）

        if sort_by == 'size':
            # サイズソート: サイズが大きい方を左に配置する
            if nodes[C1_idx]['size'] < nodes[C2_idx]['size']:
                final_order = order_C2 + order_C1 # 交換を実行
        
        elif sort_by == 'optimal' and leaf_distances is not None:
            
            # **類似度ソート（optimal）**: サイズソートの結果を完全に無視し、
            # 類似度のみに基づいて交換が必要か判定する。
            
            # 回転前: C1の右端と C2の左端 の距離
            dist_normal = leaf_distances[order_C1[-1], order_C2[0]]
            
            # 回転後: C2の右端と C1の左端 の距離
            dist_swapped = leaf_distances[order_C2[-1], order_C1[0]]
            
            # 交換後の方が近ければ、交換を実行
            if dist_swapped < dist_normal:
                final_order = order_C2 + order_C1 
            else:
                final_order = order_C1 + order_C2 
        
        # sort_by が 'size'/'optimal' 以外の場合、交換は行われない
        return final_order
    
    # --- 3. デンドログラム座標の計算 (変更なし) ---
    def calculate_x_coord(node_idx, leaf_to_x):
        node = nodes[node_idx]
        if node_idx < n_points:
            x_coord = leaf_to_x[node_idx]
            node['x'] = x_coord
            return x_coord
        x_left = calculate_x_coord(node['left'], leaf_to_x)
        x_right = calculate_x_coord(node['right'], leaf_to_x)
        x_coord = (x_left + x_right) / 2.0
        node['x'] = x_coord
        return x_coord

    # --- 4. 座標計算の実行 (変更なし) ---
    root_node_idx = n_points - 1 + (n_points - 1)
    leaf_order = get_leaf_order_sorted(root_node_idx)
    
    leaf_to_x = {leaf_idx: 2 * i + 1 for i, leaf_idx in enumerate(leaf_order)}
    calculate_x_coord(root_node_idx, leaf_to_x)

    icoord = []
    dcoord = []
    for i in range(n_points - 1):
        P = n_points + i
        C1 = nodes[P]['left']
        C2 = nodes[P]['right']
        y_P = nodes[P]['y']
        y_C1 = nodes[C1]['y']
        y_C2 = nodes[C2]['y']
        x_P = nodes[P]['x']
        x_C1 = nodes[C1]['x']
        x_C2 = nodes[C2]['x']
        icoord.append([x_C1, x_C1, x_C2, x_C2])
        dcoord.append([y_C1, y_P, y_P, y_C2])

    return icoord, dcoord, leaf_order

In [96]:
import numpy as np
# Linkage Matrixの構造を利用しないソートロジック
from scipy.optimize import linear_sum_assignment # TSPの厳密解には向かないが、順序付けに利用可能

def compute_dendrogram_coords_force_order(Z, n_points, leaf_distances=None, sort_by='size'):
    """
    Z行列の構造を無視して、葉ノードの線形順序を距離に基づいて強制的に決定します。
    これにより、デンドログラムのトポロジーが破壊される可能性があります。
    """
    # ... (1. ノード情報の準備: 変更なし) ...
    n_nodes = 2 * n_points - 1
    nodes = [{'x': None, 'y': 0.0, 'size': 1, 'left': None, 'right': None} for _ in range(n_points)]

    for i in range(n_points - 1):
        c1, c2, dist, count = Z[i]
        nodes.append({
            'x': None,
            'y': float(dist),
            'size': int(count),
            'left': int(c1),
            'right': int(c2)
        })

    # --- 2. ソートロジックの定義 (大きく変更) ---
    
    # Z行列の再帰構造を利用せず、葉ノードの順序を強制決定する関数
    def get_forced_leaf_order(n_points, leaf_distances):
        if leaf_distances is None:
            # 距離行列がない場合は、デフォルトの順序 (0, 1, 2, ...) を返す
            return list(range(n_points))
        
        # すべての葉ノードID (0, 1, ..., N-1)
        all_leaf_ids = list(range(n_points))

        # 【簡略化されたTSP近似解法】
        # 0番目の葉ノードから出発し、最も近い未訪問の葉ノードを順に繋いでいく（ニアレストネイバー法）
        
        start_id = 0
        current_id = start_id
        ordered_ids = [start_id]
        
        # 訪問済みリスト
        unvisited_ids = set(all_leaf_ids)
        unvisited_ids.remove(start_id)

        while unvisited_ids:
            # 現在の葉ノードから最も近い未訪問の葉ノードを探す
            min_dist = np.inf
            next_id = None
            
            for check_id in unvisited_ids:
                # 距離行列から距離を取得
                dist = leaf_distances[current_id, check_id] 
                
                if dist < min_dist:
                    min_dist = dist
                    next_id = check_id
            
            if next_id is not None:
                ordered_ids.append(next_id)
                unvisited_ids.remove(next_id)
                current_id = next_id
            else:
                 # すべての未訪問ノードをチェックした
                 break 
                 
        return ordered_ids

    # --- X軸順序の決定 ---
    root_node_idx = n_points - 1 + (n_points - 1)
    
    if sort_by == 'force_order':
        # Z行列の構造を無視し、距離行列のみに基づいて葉ノードのX軸順序を決定
        leaf_order = get_forced_leaf_order(n_points, leaf_distances)
    else:
        # 従来のソート（サイズまたはoptimal）は、元の get_leaf_order_sorted を利用
        # （ここでは、get_leaf_order_sorted の定義が省略されているため、仮の処理）
        # leaf_order = get_leaf_order_sorted_original(root_node_idx, nodes, leaf_distances, sort_by, n_points)
        pass  # ここに元の get_leaf_order_sorted のロジックを挿入する必要があります
        
    # 
    
    # --- 3. デンドログラム座標の計算 (変更なし) ---
    def calculate_x_coord(node_idx, leaf_to_x):
        node = nodes[node_idx]
        if node_idx < n_points:
            x_coord = leaf_to_x[node_idx]
            node['x'] = x_coord
            return x_coord
        x_left = calculate_x_coord(node['left'], leaf_to_x)
        x_right = calculate_x_coord(node['right'], leaf_to_x)
        x_coord = (x_left + x_right) / 2.0
        node['x'] = x_coord
        return x_coord

    # --- 4. 座標計算の実行 ---
    leaf_to_x = {leaf_idx: 2 * i + 1 for i, leaf_idx in enumerate(leaf_order)}
    calculate_x_coord(root_node_idx, leaf_to_x)

    icoord = []
    dcoord = []
    for i in range(n_points - 1):
        P = n_points + i
        C1 = nodes[P]['left']
        C2 = nodes[P]['right']
        # (Y軸はZ行列のデータ通り)
        y_P = nodes[P]['y']
        y_C1 = nodes[C1]['y']
        y_C2 = nodes[C2]['y']
        
        # (X軸は強制的にソートされた順序に基づいて計算された値)
        x_P = nodes[P]['x']
        x_C1 = nodes[C1]['x']
        x_C2 = nodes[C2]['x']
        
        # 強制順序では、x_C1 < x_P < x_C2 の関係が崩れる可能性がある
        icoord.append([x_C1, x_C1, x_C2, x_C2])
        dcoord.append([y_C1, y_P, y_P, y_C2])

    return icoord, dcoord, leaf_order

# flag

In [127]:
def get_linkage_matrix_from_hdbscan(condensed_tree):
    """
    (child1, child2, parent, lambda_val, count)
    """
    print("Generating linkage matrix from HDBSCAN condensed tree...")
    linkage_matrix = []
    raw_tree = condensed_tree._raw_tree
    condensed_tree = condensed_tree.to_pandas()
    cluster_tree = condensed_tree[condensed_tree['child_size'] > 1]
    sorted_condensed_tree = cluster_tree.sort_values(by=['lambda_val','parent'], ascending=True)
    print(f"len of sorted condensed tree: {len(sorted_condensed_tree)}")

    for i in range(0, len(sorted_condensed_tree), 2):
    
        # 偶数行（i）と次の奇数行（i+1）をペアとして取得
        if i + 1 < len(sorted_condensed_tree):
            
            row_a = sorted_condensed_tree.iloc[i]
            row_b = sorted_condensed_tree.iloc[i+1]
            
            # **前提チェック**: lambda_valが同じであることを確認
            if row_a['lambda_val'] != row_b['lambda_val']:
                # lambda_valが異なる場合は、次の処理に進む（結合の前提が崩れる）
                raise ValueError(f"Lambda value mismatch at rows {i} and {i+1}: {row_a['lambda_val']} vs {row_b['lambda_val']}")
                
            # Parent IDが同じであることを確認 (同じ結合の結果である可能性が高い)
            if row_a['parent'] != row_b['parent']:
                # Parent IDが異なる場合は、このペアは単一の結合ではない可能性が高い
                raise ValueError(f"Parent ID mismatch at rows {i} and {i+1}: {row_a['parent']} vs {row_b['parent']}")
            
            child_a = row_a['child']
            child_b = row_b['child']
            lam = row_a['lambda_val']
            
            # count (サイズ) は、結合された2つの子ノードのサイズ合計を使うのが論理的だが、
            # HDBSCANは親ノードのサイズをリストで持っているため、ここではそのサイズを使用
            # より正確には、このParent IDを持つ全子ノードのサイズの合計を使うべきだが、
            # 2行の child_size の合計で暫定的に対応
            # total_size = row_a['child_size'] + row_b['child_size']


            total_size = raw_tree[raw_tree['child'] == row_a['parent']]['child_size']
            if len(total_size) == 0:
                total_size = row_a['child_size'] + row_b['child_size']
            else:
                total_size = total_size[0]
            # print(total_size)
            parent_id = row_a['parent']

            linkage_matrix.append([
                int(child_a), 
                int(child_b), 
                int(parent_id),
                lam, 
                total_size,
                row_a['child_size'],
                row_b['child_size']
        ])   
    print(f"len of linkage matrix: {len(linkage_matrix)}")


    # 葉ノードに0-N-1のIDを振る
    node_id_map = {}
    current_id = 0
    leaves = _get_leaves(raw_tree)
    print(f"Number of leaves: {len(leaves)}")

    for leaf in leaves:
        node_id_map[int(leaf)] = current_id
        current_id += 1

    print(f"Leaf ID Map Size: {len(node_id_map)}")
    print(f"current id: {current_id}")

    # 結合ノードにIDを振る(linkage matrixのparent)
    for row in linkage_matrix.__reversed__():
        parent_id = row[2]
        if parent_id not in node_id_map:
            node_id_map[parent_id] = current_id
            current_id += 1

        else:
            print(f"Duplicate Parent ID found: {parent_id}")
            raise ValueError(f"Node ID {parent_id} already assigned!")
    print(f"Total Node ID Map Size: {len(node_id_map)}")
    print(f"current_id: {current_id}")

    # linkage matrixを書き換え
    max_lambda = max(row[3] for row in linkage_matrix)
    print(f"Max Lambda: {max_lambda}")
    linkage_matrix_mapped = [ 
        [node_id_map[row[0]], 
         node_id_map[row[1]], 
         node_id_map[row[2]], 
         max_lambda - row[3], 
         row[4],
         row[5],
         row[6]
        ] 
        for row in linkage_matrix.__reversed__()
    ]

    return np.array(linkage_matrix_mapped), node_id_map # linkage matrix, parentid -> newid

In [165]:
import numpy as np

def compute_dendrogram_coords_conditional(Z, n_points, allow_crossover_flags, leaf_distances=None, sort_by='size'):
    """
    Linkage Matrixからデンドログラム描画用の座標を計算します。
    allow_crossover_flags に基づいて、各結合ノードの枝の回転を制御します。
    
    Args:
        Z (np.ndarray): Linkage Matrix ((N-1) x 4)。
        n_points (int): リーフノードの総数 N。
        allow_crossover_flags (list or np.ndarray):
            Zの行数と同じ長さのブーリアン配列。True: 構造破壊ソートを適用 (距離最小化)。
        leaf_distances (np.ndarray): 葉ノード間の距離行列 (N x N)。
        sort_by (str): 'size' または 'optimal'。
                       allow_crossover_flags が False の場合に適用される標準ソート。
    """
    
    # --- 1. ノード情報の準備とフラグインデックスの付与 ---
    n_nodes = 2 * n_points - 1
    nodes = [{'x': None, 'y': 0.0, 'size': 1, 'left': None, 'right': None, 'flag_idx': -1} for _ in range(n_points)]

    for i in range(n_points - 1):
        c1, c2, dist, count = Z[i]
        nodes.append({
            'x': None,
            'y': float(dist),
            'size': int(count),
            'left': int(c1),
            'right': int(c2),
            'flag_idx': i # Z行列のi番目のマージに対応
        })

    # --- 2. ソートロジックの定義 (条件付き回転ロジック) ---
    
    def get_leaf_order_conditional(node_idx, allow_flags, leaf_dist):
        node = nodes[node_idx]
        if node_idx < n_points:
            return [node_idx]
        
        C1_idx, C2_idx = node['left'], node['right']

        # 左右の枝に含まれるリーフノードの順序を再帰的に取得 (ボトムアップ処理)
        order_C1 = get_leaf_order_conditional(C1_idx, allow_flags, leaf_dist)
        order_C2 = get_leaf_order_conditional(C2_idx, allow_flags, leaf_dist)
        
        # --- 枝の交換決定ロジック ---
        
        # 該当ノードのフラグを取得
        flag_idx = node['flag_idx']
        allow_crossover = allow_flags[flag_idx]
        
        # デフォルト順序
        final_order = order_C1 + order_C2 
        
        # 1. 構造破壊（交差許容）分岐 - フラグがTrueの場合
        if allow_crossover and leaf_dist is not None:
            # print(f"Node {node_idx}: Applying crossover-allowed sorting...")
            # 強制的な距離最小化ソートを適用
            
            # 回転前: C1の右端と C2の左端 の距離
            print(order_C1[-1], order_C2[0])
            dist_normal = leaf_dist[order_C1[-1], order_C2[0]]
            
            # 回転後: C2の右端と C1の左端 の距離
            dist_swapped = leaf_dist[order_C2[-1], order_C1[0]]
            
            # 交換後の方が近ければ、サイズソートの結果を無視して交換を強制
            if dist_swapped < dist_normal:
                final_order = order_C2 + order_C1 
            else:
                final_order = order_C1 + order_C2 
            
        # 2. 構造維持（交差不許可）分岐 - フラグがFalseの場合
        else:
            # 標準的なデンドログラムソートを適用
            current_C1, current_C2 = order_C1, order_C2
            
            if sort_by == 'size':
                # サイズソート: サイズが大きい方を左に配置
                if nodes[C1_idx]['size'] < nodes[C2_idx]['size']:
                    current_C1, current_C2 = order_C2, order_C1 
                final_order = current_C1 + current_C2 
            
            elif sort_by == 'optimal' and leaf_dist is not None:
                # 従来のOptimal Leaf Ordering (O.L.O.)ソート
                dist_normal = leaf_dist[order_C1[-1], order_C2[0]]
                dist_swapped = leaf_dist[order_C2[-1], order_C1[0]]
                
                if dist_swapped < dist_normal:
                    final_order = order_C2 + order_C1 
                else:
                    final_order = order_C1 + order_C2
            
            # sort_byが指定されていない場合は、Z行列のデフォルト順序 (交換なし)

        return final_order
    
    # --- 3. X座標計算関数 (変更なし) ---
    def calculate_x_coord(node_idx, leaf_to_x):
        node = nodes[node_idx]
        if node_idx < n_points:
            x_coord = leaf_to_x[node_idx]
            node['x'] = x_coord
            return x_coord
        x_left = calculate_x_coord(node['left'], leaf_to_x)
        x_right = calculate_x_coord(node['right'], leaf_to_x)
        x_coord = (x_left + x_right) / 2.0
        node['x'] = x_coord
        return x_coord

    # --- 4. 座標計算の実行 ---
    root_node_idx = n_points - 1 + (n_points - 1)
    
    # 条件付きソートを実行
    leaf_order = get_leaf_order_conditional(root_node_idx, allow_crossover_flags, leaf_distances)
    
    leaf_to_x = {leaf_idx: 2 * i + 1 for i, leaf_idx in enumerate(leaf_order)}
    calculate_x_coord(root_node_idx, leaf_to_x)

    # --- 5. 座標の抽出 ---
    icoord = []
    dcoord = []
    for i in range(n_points - 1):
        P = n_points + i
        C1 = nodes[P]['left']
        C2 = nodes[P]['right']
        y_P = nodes[P]['y']
        y_C1 = nodes[C1]['y']
        y_C2 = nodes[C2]['y']
        x_P = nodes[P]['x']
        x_C1 = nodes[C1]['x']
        x_C2 = nodes[C2]['x']
        
        # X軸の交差を許容する並べ替えが行われた場合、ここで線が交差（ねじれ）ます。
        icoord.append([x_C1, x_C1, x_C2, x_C2])
        dcoord.append([y_C1, y_P, y_P, y_C2])

    return icoord, dcoord, leaf_order

In [140]:
import numpy as np

def calculate_crossover_flags_from_size_array(child_sizes_array, threshold_ratio=0.2):
    """
    結合される二つの子クラスタのサイズ配列から、Crossover 許容フラグを計算します。
    
    構造破壊（Crossover = True）を許容する基準:
    結合される二つの子クラスタのサイズ比率 (min(size1, size2) / max(size1, size2)) が
    特定の閾値 (threshold_ratio) より小さい場合。
    
    Args:
        child_sizes_array (np.ndarray): 各結合における子ノードのサイズ [(size1, size2), ...], 形状は (N_merges, 2)。
        threshold_ratio (float): サイズ比率がこの閾値より小さい場合に True とする閾値 (0.0～1.0)。
        
    Returns:
        np.ndarray: 各結合に対応するブーリアンの Crossover 許容フラグ配列 (N_merges, )。
    """
    
    if child_sizes_array.ndim != 2 or child_sizes_array.shape[1] != 2:
        raise ValueError("child_sizes_array は形状 (N, 2) のNumpy配列である必要があります。")
    
    # 結合ノードの数
    n_merges = child_sizes_array.shape[0]
    
    # サイズの最小値と最大値を取得
    min_sizes = np.min(child_sizes_array, axis=1)
    max_sizes = np.max(child_sizes_array, axis=1)
    
    # サイズ比率を計算 (min / max)
    # max_sizes が 0 の場合は、ゼロ割を防ぐために np.divide の out パラメータを使用
    # 結果として比率は 0 になります (0 / 0 ではない限り)
    ratio = np.divide(min_sizes, max_sizes, out=np.zeros_like(min_sizes, dtype=float), where=max_sizes!=0)
    
    # 構造破壊の条件: 比率が小さい（アンバランスな結合）
    # ratio < threshold_ratio の場合、True (構造破壊を許容)
    crossover_flags = ratio < threshold_ratio

    # for i, c in enumerate(crossover_flags):
    #     if not c:
    #         print(f"False detected at index {i}")
    #         print(ratio[i])
    #         print(min_sizes[i], max_sizes[i])
    
    print(f"構造破壊閾値 (threshold_ratio): {threshold_ratio}")
    print(f"Crossover 許容数: {np.sum(crossover_flags)} / {n_merges}")
    
    return crossover_flags

In [172]:
import numpy as np

def compute_dendrogram_coords_conditional(Z, n_points, allow_crossover_flags, leaf_distances=None, sort_by='size'):
    """
    Linkage Matrixからデンドログラム描画用の座標を計算します。
    allow_crossover_flags に基づいて、各結合ノードの枝の回転を制御します。
    
    Args:
        Z (np.ndarray): Linkage Matrix (N-1) x 4, [c1, c2, d, count] 形式。
        n_points (int): リーフノードの総数 N。
        allow_crossover_flags (list or np.ndarray):
            Zの行数と同じ長さのブーリアン配列。True: 構造破壊ソートを適用 (距離最小化)。
        leaf_distances (np.ndarray): 葉ノード間の距離行列 (N x N)。
        sort_by (str): 'size' または 'optimal'。
                       allow_crossover_flags が False の場合に適用される標準ソート。
                       
    Returns:
        icoord (list): X軸座標のリスト。
        dcoord (list): Y軸座標のリスト。
        leaf_order (list): 最終的な葉ノードの並び順 (X軸順)。
    """
    
    # --- 1. ノード情報の準備とフラグインデックスの付与 ---
    n_nodes = 2 * n_points - 1
    # リーフノードの初期化 (flag_idx = -1)
    nodes = [{'x': None, 'y': 0.0, 'size': 1, 'left': None, 'right': None, 'flag_idx': -1} for _ in range(n_points)]

    # 結合ノードの初期化 (flag_idx = Zの行インデックス)
    for i in range(n_points - 1):
        c1, c2, dist, count = Z[i]
        nodes.append({
            'x': None,
            'y': float(dist),
            'size': int(count),
            'left': int(c1),
            'right': int(c2),
            'flag_idx': i # Z行列のi番目のマージに対応
        })

    # --- 2. ソートロジックの定義 (条件付き回転ロジック) ---
    
    def get_leaf_order_conditional(node_idx, allow_flags, leaf_dist):
        node = nodes[node_idx]
        if node_idx < n_points:
            return [node_idx]
        
        C1_idx, C2_idx = node['left'], node['right']

        # 左右の枝に含まれるリーフノードの順序を再帰的に取得
        order_C1 = get_leaf_order_conditional(C1_idx, allow_flags, leaf_dist)
        order_C2 = get_leaf_order_conditional(C2_idx, allow_flags, leaf_dist)
        
        # --- 枝の交換決定ロジック ---
        
        flag_idx = node['flag_idx']
        if flag_idx >= len(allow_flags) or flag_idx == -1:
            allow_crossover = False
        else:
            allow_crossover = allow_flags[flag_idx]
        
        # デフォルト順序 (交換なし)
        final_order = order_C1 + order_C2 
        
        # 1. 構造破壊（交差許容）分岐 - フラグがTrueの場合
        if allow_crossover and leaf_dist is not None:
            # **構造破壊を許容する強制的な近接ソート**
            
            # このノードPに含まれる全ての子孫リーフノードIDの集合
            current_leaf_ids = order_C1 + order_C2
            n_current_leaves = len(current_leaf_ids)
            
            # IDを新しいインデックス (0, 1, ..., N_current_leaves-1) にマッピング
            old_id_to_local_idx = {old_id: local_idx for local_idx, old_id in enumerate(current_leaf_ids)}
            
            # 距離行列D_local を作成
            D_local = leaf_dist[np.ix_(current_leaf_ids, current_leaf_ids)]
            
            # 【強制ソートロジック: 簡易TSP解法 (ニアレストネイバー法)】
            
            start_local_idx = 0 # 最初の葉ノードを固定
            current_local_idx = start_local_idx
            ordered_local_indices = [start_local_idx]
            
            unvisited_local_indices = set(range(n_current_leaves))
            unvisited_local_indices.remove(start_local_idx)

            while unvisited_local_indices:
                min_dist = np.inf
                next_local_idx = None
                
                for check_idx in unvisited_local_indices:
                    dist = D_local[current_local_idx, check_idx] 
                    
                    if dist < min_dist:
                        min_dist = dist
                        next_local_idx = check_idx
                
                if next_local_idx is not None:
                    ordered_local_indices.append(next_local_idx)
                    unvisited_local_indices.remove(next_local_idx)
                    current_local_idx = next_local_idx
                else:
                    break 
                    
            # 新しい順序を元のリーフ ID に戻す
            final_order = [current_leaf_ids[local_idx] for local_idx in ordered_local_indices]
            
        # 2. 構造維持（交差不許可）分岐 - フラグがFalseの場合 (変更なし)
        else:
            # 標準的なデンドログラムソートを適用 (サイズ or OLO)
            current_C1, current_C2 = order_C1, order_C2
            
            if sort_by == 'size':
                if nodes[C1_idx]['size'] < nodes[C2_idx]['size']:
                    current_C1, current_C2 = order_C2, order_C1 
                final_order = current_C1 + current_C2 
            
            elif sort_by == 'optimal' and leaf_dist is not None:
                dist_normal = leaf_dist[order_C1[-1], order_C2[0]]
                dist_swapped = leaf_dist[order_C2[-1], order_C1[0]]
                
                if dist_swapped < dist_normal:
                    final_order = order_C2 + order_C1 
                else:
                    final_order = order_C1 + order_C2

        return final_order
    
    # --- 3. X座標計算関数 (変更なし) ---
    def calculate_x_coord(node_idx, leaf_to_x):
        node = nodes[node_idx]
        if node_idx < n_points:
            x_coord = leaf_to_x[node_idx]
            node['x'] = x_coord
            return x_coord
        x_left = calculate_x_coord(node['left'], leaf_to_x)
        x_right = calculate_x_coord(node['right'], leaf_to_x)
        x_coord = (x_left + x_right) / 2.0
        node['x'] = x_coord
        return x_coord

    # --- 4. 座標計算の実行 ---
    root_node_idx = n_points - 1 + (n_points - 1)
    
    # 条件付きソートを実行
    leaf_order = get_leaf_order_conditional(root_node_idx, allow_crossover_flags, leaf_distances)
    
    leaf_to_x = {leaf_idx: 2 * i + 1 for i, leaf_idx in enumerate(leaf_order)}
    calculate_x_coord(root_node_idx, leaf_to_x)

    # --- 5. 座標の抽出 ---
    icoord = []
    dcoord = []
    for i in range(n_points - 1):
        P = n_points + i
        C1 = nodes[P]['left']
        C2 = nodes[P]['right']
        y_P = nodes[P]['y']
        y_C1 = nodes[C1]['y']
        y_C2 = nodes[C2]['y']
        x_P = nodes[P]['x']
        x_C1 = nodes[C1]['x']
        x_C2 = nodes[C2]['x']
        
        icoord.append([x_C1, x_C1, x_C2, x_C2])
        dcoord.append([y_C1, y_P, y_P, y_C2])

    return icoord, dcoord, leaf_order

In [191]:
# クラスタサイズの歪な凝集(大きいと小さい)はTrueに設定
# node sizesの辞書
linkage_matrix, node_id_map = get_linkage_matrix_from_hdbscan(condensed_tree)
cross_over_flags = np.array(calculate_crossover_flags_from_size_array(linkage_matrix[:, 5:7], threshold_ratio=0.00020))

Generating linkage matrix from HDBSCAN condensed tree...
len of sorted condensed tree: 884
len of linkage matrix: 442
884
Number of leaves: 443
Leaf ID Map Size: 443
current id: 443
Total Node ID Map Size: 885
current_id: 885
Max Lambda: 2.4746105670928955
構造破壊閾値 (threshold_ratio): 0.0002
Crossover 許容数: 62 / 442


In [192]:

# cross_over_flags = np.array([False] * (linkage_matrix.shape[0]))
icoord, dcoord, leaf_order = compute_dendrogram_coords_conditional(linkage_matrix[:, [0,1,3,4]], n_clusters, allow_crossover_flags=cross_over_flags, leaf_distances=cluster_similarity, sort_by='optimal')
segments = get_dendrogram_segments(icoord, dcoord)
plot_dendrogram_plotly(segments).show()

In [94]:
icoord, dcoord, leaf_order = compute_dendrogram_coords_bottom_up(linkage_matrix[:, [0,1,3,4]], n_clusters, leaf_distances=cluster_similarity, sort_by="optimal")
segments = get_dendrogram_segments(icoord, dcoord)
plot_dendrogram_plotly(segments).show()

In [92]:
icoord, dcoord, leaf_order = compute_dendrogram_coords_2(linkage_matrix[:, [0,1,3,4]], n_clusters, leaf_distances=cluster_similarity, sort_by="optimal", bottom_up=False, allow_cross=True)
segments = get_dendrogram_segments(icoord, dcoord)
plot_dendrogram_plotly(segments).show()

Using top-down ordering...


# 特定のクラスタ群のみ描画

In [75]:
import numpy as np

def compute_dendrogram_coords_filtered(Z, n_points, target_leaf_ids, leaf_distances=None, sort_by='optimal'):
    """
    Linkage Matrixからデンドログラム描画用の座標を計算し、
    target_leaf_idsに含まれる葉ノードのみのレイアウトを計算します。
    """
    # --- 1. ノード情報の準備 (変更なし) ---
    n_nodes = 2 * n_points - 1
    nodes = [{'x': None, 'y': 0.0, 'size': 1, 'left': None, 'right': None} for _ in range(n_points)]

    for i in range(n_points - 1):
        c1, c2, dist, count = Z[i]
        nodes.append({
            'x': None,
            'y': float(dist),
            'size': int(count),
            'left': int(c1),
            'right': int(c2)
        })

    # --- 2. ソートロジックの定義 (元のロジックを保持) ---
    
    def get_leaf_order_sorted(node_idx):
        node = nodes[node_idx]
        if node_idx < n_points:
            return [node_idx]
        
        C1_idx, C2_idx = node['left'], node['right']

        # 左右の枝に含まれるリーフノードの順序を再帰的に取得
        order_C1 = get_leaf_order_sorted(C1_idx)
        order_C2 = get_leaf_order_sorted(C2_idx)
        
        # --- 枝の交換決定ロジック (元のソートロジック) ---
        current_C1, current_C2 = order_C1, order_C2
        
        # 1. サイズソート
        if nodes[C1_idx]['size'] < nodes[C2_idx]['size']:
            current_C1, current_C2 = order_C2, order_C1 
        final_order = current_C1 + current_C2 

        # 2. 類似度ソート (上書き)
        if sort_by == 'optimal' and leaf_distances is not None:
            dist_normal = leaf_distances[order_C1[-1], order_C2[0]]
            dist_swapped = leaf_distances[order_C2[-1], order_C1[0]]
            
            if dist_swapped < dist_normal:
                final_order = order_C2 + order_C1 
            else:
                final_order = order_C1 + order_C2 

        return final_order

    # --- X座標計算関数の修正 (フィルタリングロジック追加) ---
    
    def calculate_x_coord(node_idx, leaf_to_x):
        node = nodes[node_idx]
        
        if node_idx < n_points:
            # リーフノードの場合
            x_coord = leaf_to_x.get(node_idx)
            # フィルタリングされた葉に含まれない場合、X座標を-1としてマーク
            node['x'] = x_coord if x_coord is not None else -1 
            return node['x']
        
        # 結合ノードの場合: 再帰的にX座標を取得
        x_left = calculate_x_coord(node['left'], leaf_to_x)
        x_right = calculate_x_coord(node['right'], leaf_to_x)
        
        # 左右の子ノードが両方とも非表示ノードからの枝の場合、この枝も非表示（X=-1）
        if x_left == -1 and x_right == -1:
            node['x'] = -1
            return -1
        
        # 左右どちらか、または両方が表示対象の場合:
        # X座標は、表示されている子のX座標の中間点、または単独の子のX座標
        if x_left != -1 and x_right != -1:
            # 両方表示の場合: 中央値
            x_coord = (x_left + x_right) / 2.0
        else:
            # 片方のみ表示の場合: 表示されている側のX座標を使用 (線がまっすぐ伸びる)
            x_coord = x_left if x_left != -1 else x_right
            
        node['x'] = x_coord
        return x_coord


    # --- 3. デンドログラム座標の計算とフィルタリング ---
    root_node_idx = n_points - 1 + (n_points - 1)
    
    # 3.1. 全リーフノードの順序を取得 (ソート実行)
    full_leaf_order = get_leaf_order_sorted(root_node_idx)

    # 3.2. 描画対象の葉のみを抽出
    filtered_leaf_order = [
        leaf_id for leaf_id in full_leaf_order if leaf_id in target_leaf_ids
    ]
    
    # 3.3. X座標を再割り当て
    # フィルタリングされた順序に基づいて、X座標を 1, 3, 5, ... と詰めて割り当てる
    leaf_to_x = {leaf_id: 2 * i + 1 for i, leaf_id in enumerate(filtered_leaf_order)}
    
    # 3.4. X座標の計算 (非表示ノードは-1が割り当てられる)
    calculate_x_coord(root_node_idx, leaf_to_x)

    # 3.5. 座標情報の抽出とフィルタリング
    icoord = []
    dcoord = []
    
    for i in range(n_points - 1):
        P = n_points + i
        C1 = nodes[P]['left']
        C2 = nodes[P]['right']
        
        x_C1 = nodes[C1]['x']
        x_C2 = nodes[C2]['x']
        
        # 両端のX座標が有効である（-1ではない）場合のみ、線分を描画
        if x_C1 != -1 and x_C2 != -1:
            y_P = nodes[P]['y']
            y_C1 = nodes[C1]['y']
            y_C2 = nodes[C2]['y']
            
            icoord.append([x_C1, x_C1, x_C2, x_C2])
            dcoord.append([y_C1, y_P, y_P, y_C2])

    # 4. 最終的な順序を返す
    return icoord, dcoord, filtered_leaf_order

In [78]:
selected_leaf_ids = list(range(0, n_clusters, 2))  # 例: 10個おきに選択
icoord, dcoord, leaf_order = compute_dendrogram_coords_filtered(linkage_matrix[:, [0,1,3,4]], n_clusters, selected_leaf_ids, leaf_distances=cluster_similarity, sort_by='optimal')
segments = get_dendrogram_segments(icoord, dcoord)
plot_dendrogram_plotly(segments).show()

In [79]:
import numpy as np

def create_sub_linkage_matrix(Z_full, n_points_full, target_leaf_ids):
    """
    Linkage Matrix (Z_full) から、指定されたリーフIDを含むサブツリーの
    新しい Linkage Matrix を生成します。
    
    Args:
        Z_full (np.ndarray): 元のデンドログラムの Linkage Matrix ((N-1) x 4)。
        n_points_full (int): 元のデンドログラムの全リーフノード数 N。
        target_leaf_ids (list): 新しい Linkage Matrix に含めたい葉ノードのIDリスト。

    Returns:
        np.ndarray: 新しい Linkage Matrix (Z_new)。
        int: 新しいデンドログラムのリーフノード数 N_new。
    """
    
    # 1. ノード構造の準備 (元のZ行列に基づく全ノード)
    nodes_full = {}
    
    # リーフノードの構造を保存
    for i in range(n_points_full):
        nodes_full[i] = {'leaf': True, 'count': 1, 'children': None, 'distance': 0.0}

    # 結合ノードの構造を保存 (インデックスは n_points_full から開始)
    for i, row in enumerate(Z_full):
        p_idx = n_points_full + i
        c1, c2, dist, count = map(int, row[:4])
        nodes_full[p_idx] = {
            'leaf': False, 
            'count': count, 
            'distance': row[2], 
            'children': (c1, c2)
        }
        
    root_node_idx = n_points_full - 1 + (n_points_full - 1)
    
    # 2. サブツリーのルートノードを特定
    # ターゲットIDをすべて含む最小の共通祖先ノードを探す
    
    # ターゲットIDが一つもない場合はエラー
    if not target_leaf_ids:
        raise ValueError("target_leaf_ids は空であってはなりません。")

    # ターゲットIDをセットに変換し、含まれるリーフノードIDを取得する関数を定義
    def get_leaves_in_subtree(node_idx):
        if nodes_full[node_idx]['leaf']:
            return {node_idx}
        
        c1, c2 = nodes_full[node_idx]['children']
        return get_leaves_in_subtree(c1) | get_leaves_in_subtree(c2)

    # ルートから順に、ターゲットIDをすべて含む最小のサブツリーを特定
    def find_sub_root(current_idx):
        if nodes_full[current_idx]['leaf']:
            return current_idx

        c1_idx, c2_idx = nodes_full[current_idx]['children']
        
        # 子ノードに含まれるリーフIDを取得
        leaves_c1 = get_leaves_in_subtree(c1_idx)
        leaves_c2 = get_leaves_in_subtree(c2_idx)
        
        target_set = set(target_leaf_ids)
        
        # c1 にターゲットIDがすべて含まれていれば、c1 を再帰的に探索
        if target_set.issubset(leaves_c1):
            return find_sub_root(c1_idx)
        # c2 にターゲットIDがすべて含まれていれば、c2 を再帰的に探索
        elif target_set.issubset(leaves_c2):
            return find_sub_root(c2_idx)
        # ターゲットIDがc1とc2にまたがっている場合、現在のノードがサブツリーのルート
        else:
            return current_idx

    sub_root_idx = find_sub_root(root_node_idx)
    
    # 3. 新しいZ行列を構築 (インデックスの再マッピングとリセット)
    
    # 新しいリーフノード数 N_new
    N_new = len(target_leaf_ids)
    
    # 新しいインデックスを元のIDにマッピング: {元のID: 新しいID (0〜N_new-1)}
    old_id_to_new_leaf_idx = {old_id: new_idx for new_idx, old_id in enumerate(target_leaf_ids)}
    
    Z_new = []
    
    # サブツリーを探索し、Z_newを構築する関数
    # 戻り値: 新しいインデックスID (リーフなら 0〜N_new-1, 中間ノードなら N_new〜)
    def build_sub_linkage(node_idx):
        node = nodes_full[node_idx]
        
        if node['leaf']:
            # ターゲットリーフIDに含まれていなければ、エラーとして扱う（ここでは起こらないはず）
            if node_idx not in old_id_to_new_leaf_idx:
                return -1
            return old_id_to_new_leaf_idx[node_idx] # 新しいリーフインデックス
        
        c1_old, c2_old = node['children']
        
        # 再帰的に子ノードの新しいインデックスを取得
        new_c1_idx = build_sub_linkage(c1_old)
        new_c2_idx = build_sub_linkage(c2_old)
        
        # --- 結合ノードの処理 ---
        
        # 左右の子ノードが両方ともターゲットに含まれていない場合はスキップ
        if new_c1_idx == -1 and new_c2_idx == -1:
            return -1

        # 左右どちらか一方がターゲットに含まれていない場合、ノードを飛び越える（スキップ）
        if new_c1_idx == -1:
            return new_c2_idx
        if new_c2_idx == -1:
            return new_c1_idx

        # 左右両方が有効な場合、新しい結合を作成
        # 新しいノードインデックス (現在のZ_newの行数 + N_new)
        new_parent_idx = len(Z_new) + N_new 
        
        # Z 行に追加 (c1, c2 のインデックスは新しいインデックス体系を使用)
        Z_new.append([
            min(new_c1_idx, new_c2_idx), 
            max(new_c1_idx, new_c2_idx), 
            node['distance'], 
            node['count'] # count は元のままで良いが、新しいリーフ数に調整する方が正確
        ])
        
        return new_parent_idx # 新しい結合ノードのインデックスを返す

    # サブツリーの構築を開始
    build_sub_linkage(sub_root_idx)

    # Z_new を numpy 配列に変換
    Z_new_array = np.array(Z_new)
    
    # 4. 新しいリーフノードの数とZ行列を返す
    return Z_new_array, N_new